In [1]:
import zarr
import numpy as np
import pygrib
import xarray as xr
import dask as da
import sys
from datetime import datetime,timedelta,date
from numcodecs import Blosc, Zstd, LZ4
import sys
import cfgrib

In [2]:
dataloc = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/hrrr_conus/'
store = zarr.DirectoryStore(dataloc+'hrrr_forecast_20200202.zarr')

In [3]:
root = zarr.group(store=store)#, overwrite=True)

In [ ]:
groups = ['surface','atmosphere','cloudTop','heightAboveGround','isothermal','isobaricInhPa','pressureFromGroundLayer','sigmaLayer','meanSea',
          'heightAboveGroundLayer','unknown','depthBelowLand','isobaricLayer','cloudBase','nominalTop','isothermZero','adiabaticCondensation']

In [ ]:
for i in range(0,len(groups)):
    name = groups[i]
    root.create_group(name)

In [ ]:
root['heightAboveGround'].create_group('1000')
root['heightAboveGround'].create_group('4000')
root['heightAboveGround'].create_group('80')
root['heightAboveGround'].create_group('2')
root['heightAboveGround'].create_group('10')

#root['heightAboveGroundLayer'].create_group('5000')
root['heightAboveGroundLayer'].create_group('2000')
root['heightAboveGroundLayer'].create_group('3000')
root['heightAboveGroundLayer'].create_group('0')

root['isothermal'].create_group('263')
root['isothermal'].create_group('253')

root['isobaricInhPa'].create_group('250')
root['isobaricInhPa'].create_group('300')
root['isobaricInhPa'].create_group('500')
root['isobaricInhPa'].create_group('700')
root['isobaricInhPa'].create_group('850')
root['isobaricInhPa'].create_group('925')
root['isobaricInhPa'].create_group('1000')

root['pressureFromGroundLayer'].create_group('10000')
root['pressureFromGroundLayer'].create_group('18000')
root['pressureFromGroundLayer'].create_group('9000')
root['pressureFromGroundLayer'].create_group('25500')

root['sigmaLayer'].create_group('0')
root['sigmaLayer'].create_group('1')

root['isobaricLayer'].create_group('500')

In [ ]:
root['surface'].create_group('accumulated_variables')

In [7]:
import time
t1 = time.time()
fileloc = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/hrrr_conus/020220/hrrr*'


ds = xr.open_mfdataset(fileloc,engine='cfgrib', concat_dim='step',
                     backend_kwargs={'indexpath':'', 'filter_by_keys': {'stepType': 'instant', 'typeOfLevel': 'heightAboveGroundLayer', 'level': 3000}})

t2 = time.time()
print(t2-t1)

<ipython-input-7-4f81bd1dbade>:6: FutureWarning: In xarray version 0.15 the default behaviour of `open_mfdataset`
will change. To retain the existing behavior, pass
combine='nested'. To use future default behavior, pass
combine='by_coords'. See
http://xarray.pydata.org/en/stable/combining.html#combining-multi

  ds = xr.open_mfdataset(fileloc,engine='cfgrib', concat_dim='step',
/uufs/chpc.utah.edu/common/home/u1014509/miniconda3/envs/zenv/lib/python3.8/site-packages/xarray/backends/api.py:934: FutureWarning: Also `open_mfdataset` will no longer accept a `concat_dim` argument.
To get equivalent behaviour from now on please use the new
`combine_nested` function instead (or the `combine='nested'` option to
`open_mfdataset`).The datasets supplied do not have global dimension coordinates. In
future, to continue concatenating without supplying dimension
coordinates, please use the new `combine_nested` function (or the
`combine='nested'` option to open_mfdataset.
  combined = auto_combine(


563.4385349750519


In [8]:
ds = ds.chunk({'step':19, 'y':150, 'x':150})

compressor = Blosc(cname='zstd', clevel=5, shuffle=0)
encoding = {v: {'compressor': compressor, 'dtype': '<f4', '_FillValue': '-9999'} for v in ds.data_vars}

ds.to_zarr(store, group='heightAboveGroundLayer/3000', mode='w',encoding=encoding)

In [ ]:
import gc
gc.collect()

In [ ]:
grbs = pygrib.open(dataloc+'020220/hrrr.t00z.wrfsfcf06.grib2')

for grb in grbs:
    grb
    
grbs[5].level

In [ ]:
grbs[5].typeOfLevel

In [ ]:
zarrloc = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/hrrr_conus/'

In [ ]:
import numcodecs as ncd
import struct

buf = ncd.blosc.decompress(open(zarrloc+'0.0.0', 'rb').read())

chunk = np.frombuffer(buf, dtype='<f4')
chunk